# Important python packages and how to use them: scipy

scipy provides, together with numpy, a broad spectrum for numerical methods commonly used in physics. Usually, it's worth to check in advance if there are functions provided by packages that perform operations much faster than implementing it on your own with e.g. for-loops etc. 

One of those is definetly scipy, which offers a wide range of functionalities for fitting, integration, solving differential equations, statistics and so much more. What we will take a look in the next couple of minutes are the fitting capabilities and a tool to estimate correlations between data (when you reconstruct something e.g. with a regression NN and you want to check how well these data correspond to the true ones).

We import the curve_fit function from scipy, which is included in the optimize module. It uses a least squares algorithm.

In [ ]:
import numpy as np
from scipy.optimize import curve_fit

Let's create some pseudodata and inspect them

In [ ]:
x = np.linspace(0, 20)

# The data is distributed according to a function, that we define on our own
def function(x, a, b, c):
    return a * np.sin(x) + b * np.exp(-c * x)

# We add some gaussian noise to the data
y = function(x, 2.5, 1.3, 0.1) # these are the parameters we want to get back from the fit in the end
y_noise = 0.3 * np.random.normal(size = x.size)
y_noise += y

When we want to plot the data, we use the matplotlib package

In [ ]:
import matplotlib.pyplot as plt

In [ ]:
# Plot the data
plt.errorbar(x, y_noise, 
             fmt = "o",
             label = "Noisy pseudo-measurement"
)

plt.plot(x, y, label = "True function", color = "black")

plt.legend()
plt.xlabel(r"$x$-data")
plt.ylabel(r"$y$-data")

Now we want to use the curve-fit functionalities to fit the noisy data

In [ ]:
parameters, covariance_matrix = curve_fit(function, x, y_noise)

# more parameters can be provided here:
# - sigma, absolute_sigma: std. dev. of values and whether they are relative or not
# - maxfev: number of function evaluations
# - p0=[...]: initial values for fit start
# - bounds=[[...], [...]] limits for the fit

# Let's get the parameters uncertainties from the covariance matrix, which includes also the relationship and dependendy between the fit parameters
# What is the difference to the correlation?
print("Covariance matrix =\n", covariance_matrix)
parameter_uncertainties = np.sqrt(np.diag(covariance_matrix))
print("\nParameters =", parameters)
print("Parameter uncertainties =", parameter_uncertainties)

We include the fit in our plot

In [ ]:
plt.errorbar(x, y_noise, 
             fmt = "o",
             label = "Noisy pseudo-data"
)

plt.plot(x, y, label = "True function", color = "black")

# To get a smooth fit function, we create a new x-array
x_fit = np.linspace(np.min(x), np.max(x), 1001)
plt.plot(x_fit, function(x_fit, *parameters), color = "orange", label = "Fit function") # the *-notation unpacks a vector

# We can also draw the band of the fit uncertainty 
plt.fill_between(x_fit, 
                 function(x_fit, *(parameters - parameter_uncertainties)), 
                 function(x_fit, *(parameters + parameter_uncertainties)), 
                 color = "orange", alpha = 0.3
)

plt.legend()
plt.xlabel(r"$x$-data")
plt.ylabel(r"$y$-data")

We can also examine the correlation. For this, we simply assume that our fit is our reconstruction of an observable (and we create ourself much more "data")

In [ ]:
x_correlation = np.linspace(np.min(x), np.max(x), 100000)
y_true = function(x_correlation, 2.5, 1.3, 0.5)
y_reco = function(x_correlation, *parameters)

In [ ]:
# Always useful for such tasks: the 2D histogram or a scatter plot

plt.hist2d(y_true, 
           y_reco, 
           bins = 20, 
           cmap = "plasma",
)

plt.colorbar(label = "Entries")
plt.xlabel("True values")
plt.ylabel("Reconstructed values")

From the documentation (https://docs.scipy.org/doc/scipy/reference/generated/scipy.stats.pearsonr.html):
"The Pearson correlation coefficient [1] measures the linear relationship between two datasets. Like other correlation coefficients, this one varies between -1 and +1 with 0 implying no correlation. Correlations of -1 or +1 imply an exact linear relationship. Positive correlations imply that as x increases, so does y. Negative correlations imply that as x increases, y decreases."


The correlation coefficient is calculated as follows:
$$ r = \frac{\sum_{}^{} (x - \bar{x})(y - \bar{y})}{\sqrt{\sum_{}^{} (x - \bar{x})^2 \cdot \sum_{}^{} (y - \bar{y})^2}} $$

First we include the pearson correlation from scipy.stats

In [ ]:
from scipy.stats import pearsonr

correlation_result = pearsonr(y_true, y_reco)

In [ ]:
print("Statistic =", correlation_result.statistic)
print("p-value =", correlation_result.pvalue)

What does the statistic value refer to? What range does it cover?

How would it look like when our reconstruction does not correlate to our true values? Let's try it out:

In [ ]:
y_reco_uncorrelated = np.random.normal(size = y_true.size)

In [ ]:
plt.scatter(y_true, 
            y_reco_uncorrelated, 
            s = 1, alpha = 0.5
)

# plt.colorbar(label = "Entries")
plt.xlabel("True values")
plt.ylabel("Reconstructed values")

In [ ]:
correlation_result_uncorrelated = pearsonr(y_true, y_reco_uncorrelated)

print("Statistic =", correlation_result_uncorrelated.statistic)
print("p-value =", correlation_result_uncorrelated.pvalue)

What does the $p$-value refer to? Is it favorable to have a large or a small $p$-value?